In [1]:
from matplotlib import animation
import matplotlib.pyplot as plt
from pprint import pprint
import ray
import torch
%matplotlib notebook

from run import *

/home/anchorwatt/miniconda3/lib/python3.9/site-packages/ray/autoscaler/_private/cli_logger.py:57: FutureWarning: Not all Ray CLI dependencies were found. In Ray 1.4+, the Ray CLI, autoscaler, and dashboard will only be usable via `pip install 'ray[default]'`. Please update your install command.
  warnings.warn(


In [2]:
def run_evaluation(
    agent_run_names, 
    agent_checkpoints, 
    config, 
    policy_name="ppo", 
    seed=1,
    heterogeneous=True,
    num_episodes=1,
    record=True
):
    ray.shutdown()
    ray.init()
    eval_run_name = ""
    for i in range(len(agent_run_names)):
        eval_run_name += f"{agent_run_names[i]}_{agent_checkpoints[i]}_"
    eval_run_name = eval_run_name[:-1]
    ray_dir = f"{os.path.expanduser('~')}/ray_results"
    eval_results_dir = f"{ray_dir}/{eval_run_name}"
    register_env("ZSC-Cleaner", lambda _: CleanerEnv(config["env_config"], run_name=eval_run_name))

    agents = {}
    for i in range(config["env_config"]["num_agents"]):
        agent = Agent(
            policy_name=policy_name,
            run_name=agent_run_names[i],
            agent_num=i,
            config=config,
            seed=seed,
            heterogeneous=heterogeneous,
        )
        agents[agent.name] = agent
        trainer_agents = {}
        for other_agent_num in range(agent.config["env_config"]["num_agents"]):
            other_agent = deepcopy(agent)
            other_agent.agent_num = other_agent_num
            other_agent.name = f"{agent.run_name}:{other_agent_num}"
            trainer_agents[other_agent.name] = other_agent
        agent.trainer = create_trainer(
            agent.policy_name,
            trainer_agents, 
            agent.config, 
            agent.results_dir, 
            seed=agent.seed, 
            heterogeneous=agent.heterogeneous, 
            num_workers=1
        )
        checkpoint_num = agent_checkpoints[i]
        checkpoint_path = f"{ray_dir}/{agent.run_name}/checkpoint_" \
                          f"{str(checkpoint_num).zfill(6)}/checkpoint-{checkpoint_num}"
        agent.trainer.load_checkpoint(checkpoint_path)
    
    ep_rewards, ani = evaluate(
        agents,
        config,
        eval_run_name,
        heterogeneous=heterogeneous,
        num_episodes=num_episodes,
        record=record,
    )
    return ep_rewards, ani

In [3]:
def cross_play(
    run_name_0, run_name_1, checkpoint_0, checkpoint_1, config,
    heterogeneous=True, num_episodes=1
):
    num_agents = config["env_config"]["num_agents"]
    self_play_0, _ = run_evaluation(
        [run_name_0] * num_agents, 
        [checkpoint_0] * num_agents, 
        config, 
        policy_name="ppo", 
        seed=1,
        heterogeneous=heterogeneous,
        num_episodes=num_episodes,
        record=False
    )
    self_play_1, _ = run_evaluation(
        [run_name_1] * num_agents, 
        [checkpoint_1] * num_agents, 
        config, 
        policy_name="ppo", 
        seed=1,
        heterogeneous=heterogeneous,
        num_episodes=num_episodes,
        record=False
    )
    if num_agents == 2:
        run_names = [run_name_0, run_name_1]
        checkpoints = [checkpoint_0, checkpoint_1]
    elif num_agents == 4:
        run_names = [run_name_0, run_name_1, run_name_1, run_name_0]
        checkpoints = [checkpoint_0, checkpoint_1, checkpoint_1, checkpoint_0]
    elif num_agents == 5:
        run_names = [run_name_0, run_name_1, run_name_0, run_name_1, run_name_0]
        checkpoints = [checkpoint_0, checkpoint_1, checkpoint_0, checkpoint_1, checkpoint_0]
    elif num_agents == 8:
        run_names = [run_name_0, run_name_1, run_name_1, run_name_0, 
                     run_name_1, run_name_0, run_name_0, run_name_1]
        checkpoints = [checkpoint_0, checkpoint_1, checkpoint_1, checkpoint_0,
                       checkpoint_1, checkpoint_0, checkpoint_0, checkpoint_1]
    cross_play, _ = run_evaluation(
        run_names,
        checkpoints,
        config, 
        policy_name="ppo", 
        seed=1,
        heterogeneous=heterogeneous,
        num_episodes=num_episodes,
        record=False
    )
    return self_play_0, self_play_1, cross_play

In [4]:
run_name_0 = "simple123"
run_name_1 = "simple456"
config_name = "simple_2"
heterogeneous = True
max_checkpoint = 501
num_episodes = 50
random_start = False

config = load_config(config_name)
config["env_config"]["random_start"] = random_start
self_play_mean_reward_2_0 = []
self_play_mean_reward_2_1 = []
cross_play_mean_reward_2 = []
all_checkpoints = list(range(1, max_checkpoint + 1, 25))
for checkpoint in all_checkpoints:
    sp_0, sp_1, cp = cross_play(
        run_name_0, run_name_1, checkpoint, checkpoint, config,
        heterogeneous=heterogeneous, num_episodes=num_episodes
    )
    self_play_mean_reward_2_0.append(sum(sp_0) / num_episodes)
    self_play_mean_reward_2_1.append(sum(sp_1) / num_episodes)
    cross_play_mean_reward_2.append(sum(cp) / num_episodes)

2021-09-16 14:54:53,924	INFO services.py:1272 -- View the Ray dashboard at http://127.0.0.1:8265
2021-09-16 14:54:55,767	INFO trainer.py:696 -- Current log_level is WARN. For more information, set 'log_level': 'INFO' / 'DEBUG' or use the -v and -vv flags.
2021-09-16 14:54:58,389	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 14:55:00,897	WARNING util.py:53 -- Install gputil for GPU system monitoring.


<IPython.core.display.Javascript object>

episode rewards: [29.0, 34.0, 27.0, 35.0, 28.0, 39.0, 30.0, 32.0, 35.0, 35.0, 41.0, 28.0, 23.0, 30.0, 33.0, 38.0, 25.0, 18.0, 41.0, 20.0, 31.0, 32.0, 32.0, 26.0, 26.0, 43.0, 31.0, 37.0, 37.0, 41.0, 37.0, 19.0, 32.0, 26.0, 33.0, 32.0, 31.0, 29.0, 39.0, 28.0, 40.0, 40.0, 33.0, 33.0, 29.0, 24.0, 30.0, 39.0, 41.0, 18.0] (mean = 31.8)


2021-09-16 14:55:16,308	INFO services.py:1272 -- View the Ray dashboard at http://127.0.0.1:8265
2021-09-16 14:55:20,619	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 14:55:23,105	WARNING util.py:53 -- Install gputil for GPU system monitoring.


<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

episode rewards: [92.0, 92.0, 93.0, 90.0, 62.0, 75.0, 91.0, 89.0, 85.0, 83.0, 91.0, 91.0, 88.0, 91.0, 91.0, 89.0, 94.75, 74.0, 90.0, 92.0, 72.0, 92.0, 87.0, 94.75, 92.0, 86.0, 89.0, 87.0, 91.0, 81.0, 87.0, 95.5, 87.0, 91.0, 87.0, 92.0, 79.0, 89.0, 86.0, 92.0, 90.0, 91.0, 50.0, 91.0, 90.0, 91.0, 85.0, 85.0, 80.0, 76.0] (mean = 86.6)


2021-09-16 15:16:16,508	INFO services.py:1272 -- View the Ray dashboard at http://127.0.0.1:8265
2021-09-16 15:16:19,953	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:16:22,471	WARNING util.py:53 -- Install gputil for GPU system monitoring.


<IPython.core.display.Javascript object>

episode rewards: [13.0, 14.0, 10.0, 18.0, 21.0, 15.0, 17.0, 21.0, 14.0, 18.0, 17.0, 14.0, 17.0, 13.0, 14.0, 15.0, 20.0, 10.0, 19.0, 14.0, 12.0, 15.0, 31.0, 15.0, 15.0, 18.0, 16.0, 15.0, 26.0, 17.0, 24.0, 11.0, 16.0, 18.0, 14.0, 16.0, 43.0, 14.0, 15.0, 16.0, 23.0, 12.0, 16.0, 27.0, 19.0, 21.0, 26.0, 16.0, 22.0, 14.0] (mean = 17.54)


In [5]:
run_name_0 = "simple_4_123"
run_name_1 = "simple_4_456"
config_name = "simple_4"
heterogeneous = True
max_checkpoint = 501
num_episodes = 50
random_start = False

config = load_config(config_name)
config["env_config"]["random_start"] = random_start
self_play_mean_reward_4_0 = []
self_play_mean_reward_4_1 = []
cross_play_mean_reward_4 = []
all_checkpoints = list(range(1, max_checkpoint + 1, 25))
for checkpoint in all_checkpoints:
    sp_0, sp_1, cp = cross_play(
        run_name_0, run_name_1, checkpoint, checkpoint, config,
        heterogeneous=heterogeneous, num_episodes=num_episodes
    )
    self_play_mean_reward_4_0.append(sum(sp_0) / num_episodes)
    self_play_mean_reward_4_1.append(sum(sp_1) / num_episodes)
    cross_play_mean_reward_4.append(sum(cp) / num_episodes)

2021-09-16 15:16:37,178	INFO services.py:1272 -- View the Ray dashboard at http://127.0.0.1:8265
2021-09-16 15:16:41,010	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:16:43,754	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:16:46,525	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:16:49,263	WARNING util.py:53 -- Install gputil for GPU system monitoring.


<IPython.core.display.Javascript object>

episode rewards: [52.5, 59.5, 54.5, 54.5, 58.5, 66.5, 44.5, 51.5, 49.5, 62.5, 62.5, 64.5, 55.5, 56.5, 59.5, 69.5, 61.5, 51.5, 63.5, 61.5, 60.5, 46.5, 58.5, 63.5, 49.5, 68.5, 45.5, 45.5, 56.5, 63.5, 51.5, 61.5, 46.5, 53.5, 51.5, 46.5, 60.5, 57.5, 52.5, 69.5, 42.5, 54.5, 52.5, 54.5, 44.5, 44.5, 50.5, 61.5, 46.5, 63.5] (mean = 55.68)


2021-09-16 15:17:09,424	INFO services.py:1272 -- View the Ray dashboard at http://127.0.0.1:8265
2021-09-16 15:17:13,138	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:17:15,826	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:17:18,539	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:17:21,398	WARNING util.py:53 -- Install gputil for GPU system monitoring.


<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

episode rewards: [91.5, 84.5, 87.5, 87.5, 78.5, 78.5, 87.5, 80.5, 94.5, 92.5, 77.5, 72.5, 81.5, 82.5, 86.5, 78.5, 92.5, 88.5, 74.5, 73.5, 89.5, 84.5, 87.5, 89.5, 75.5, 84.5, 93.5, 91.5, 87.5, 78.5, 91.5, 89.5, 89.5, 87.5, 68.5, 90.5, 79.5, 89.5, 87.5, 84.5, 78.5, 92.5, 89.5, 80.5, 86.5, 89.5, 90.5, 89.5, 91.5, 81.5] (mean = 85.22)


2021-09-16 15:52:09,980	INFO services.py:1272 -- View the Ray dashboard at http://127.0.0.1:8265
2021-09-16 15:52:14,006	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:52:16,877	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:52:19,746	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:52:22,577	WARNING util.py:53 -- Install gputil for GPU system monitoring.


<IPython.core.display.Javascript object>

episode rewards: [73.5, 58.5, 78.5, 70.5, 64.5, 38.5, 69.5, 63.5, 53.5, 42.5, 49.5, 74.5, 63.5, 65.5, 68.5, 72.5, 29.5, 69.5, 66.5, 61.5, 51.5, 73.5, 63.5, 51.5, 57.5, 78.5, 60.5, 69.5, 51.5, 72.5, 81.5, 58.5, 69.5, 71.5, 66.5, 70.5, 53.5, 67.5, 80.5, 62.5, 67.5, 70.5, 42.5, 57.5, 59.5, 43.5, 76.5, 56.5, 67.5, 64.5] (mean = 63.04)


In [ ]:
run_name_0 = "simple_8_123"
run_name_1 = "simple_8_456"
config_name = "simple_8"
heterogeneous = True
max_checkpoint = 501
num_episodes = 50
random_start = False

config = load_config(config_name)
config["env_config"]["random_start"] = random_start
self_play_mean_reward_8_0 = []
self_play_mean_reward_8_1 = []
cross_play_mean_reward_8 = []
all_checkpoints = list(range(1, max_checkpoint + 1, 25))
for checkpoint in all_checkpoints:
    sp_0, sp_1, cp = cross_play(
        run_name_0, run_name_1, checkpoint, checkpoint, config,
        heterogeneous=heterogeneous, num_episodes=num_episodes
    )
    self_play_mean_reward_8_0.append(sum(sp_0) / num_episodes)
    self_play_mean_reward_8_1.append(sum(sp_1) / num_episodes)
    cross_play_mean_reward_8.append(sum(cp) / num_episodes)

2021-09-16 15:52:45,828	INFO services.py:1272 -- View the Ray dashboard at http://127.0.0.1:8265
2021-09-16 15:52:50,528	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:52:54,049	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:52:57,399	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:53:00,889	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:53:04,341	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:53:07,816	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:53:11,558	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:53:15,093	WARNING util.py:53 -- Install gputil for GPU system monitoring.


<IPython.core.display.Javascript object>

episode rewards: [55.0, 66.0, 59.0, 48.0, 52.0, 60.0, 65.0, 76.0, 72.0, 59.0, 58.0, 61.0, 66.0, 65.0, 77.0, 57.0, 44.0, 77.0, 59.0, 49.0, 79.0, 63.0, 66.0, 53.0, 60.0, 64.0, 57.0, 60.0, 78.0, 64.0, 53.0, 58.0, 61.0, 45.0, 61.0, 73.0, 58.0, 57.0, 69.0, 55.0, 73.0, 58.0, 63.0, 53.0, 57.0, 50.0, 69.0, 59.0, 58.0, 71.0] (mean = 61.4)


2021-09-16 15:53:39,625	INFO services.py:1272 -- View the Ray dashboard at http://127.0.0.1:8265
2021-09-16 15:53:44,094	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:53:47,521	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:53:51,007	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:53:54,538	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:53:58,038	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:54:01,518	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:54:05,059	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:54:08,572	WARNING util.py:53 -- Install gputil for GPU system monitoring.


<IPython.core.display.Javascript object>

...

episode rewards: [75.0, 79.0, 79.0, 79.0, 64.0, 81.0, 72.0, 81.0, 75.0, 80.0, 79.0, 69.0, 77.0, 78.0, 84.0, 85.0, 66.0, 78.0, 84.0, 79.0, 71.0, 78.0, 69.0, 79.0, 72.0, 75.0, 76.0, 75.0, 69.0, 74.0, 70.0, 78.0, 65.0, 74.0, 74.0, 75.0, 86.0, 68.0, 75.0, 70.0, 82.0, 73.0, 78.0, 80.0, 80.0, 74.0, 69.0, 73.0, 69.0, 66.0] (mean = 75.22)


2021-09-16 15:57:26,543	INFO services.py:1272 -- View the Ray dashboard at http://127.0.0.1:8265
2021-09-16 15:57:31,209	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:57:34,774	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:57:38,287	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:57:41,815	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:57:45,440	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:57:49,105	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:57:52,575	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:57:56,104	WARNING util.py:53 -- Install gputil for GPU system monitoring.


<IPython.core.display.Javascript object>

episode rewards: [72.0, 79.0, 75.0, 72.0, 79.0, 74.0, 74.0, 82.0, 75.0, 77.0, 61.0, 75.0, 72.0, 70.0, 68.0, 69.0, 73.0, 71.0, 64.0, 71.0, 74.0, 71.0, 69.0, 78.0, 70.0, 66.0, 81.0, 68.0, 63.0, 81.0, 71.0, 69.0, 82.0, 78.0, 79.0, 86.0, 76.0, 63.0, 81.0, 63.0, 69.0, 73.0, 64.0, 78.0, 63.0, 69.0, 78.0, 64.0, 64.0, 74.0] (mean = 72.36)


2021-09-16 15:58:23,863	INFO services.py:1272 -- View the Ray dashboard at http://127.0.0.1:8265
2021-09-16 15:58:28,245	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:58:31,777	WARNING util.py:53 -- Install gputil for GPU system monitoring.
2021-09-16 15:58:35,287	WARNING util.py:53 -- Install gputil for GPU system monitoring.


In [ ]:
%matplotlib inline
all_checkpoints = list(range(1, 502, 25))
fig, (ax1, ax2, ax3) = plt.subplots(1, 3, figsize=(12, 3))
ax1.set_title("2 agents")
ax1.set_ylim(0, 100)
ax1.plot(all_checkpoints, self_play_mean_reward_2_0, label="self-play (seed 123)")
ax1.plot(all_checkpoints, self_play_mean_reward_2_1, label="self-play (seed 456)")
ax1.plot(all_checkpoints, cross_play_mean_reward_2, label="cross-play")
ax1.set_xlabel("Episode")
ax1.set_ylabel("Reward")

ax2.set_title("4 agents")
ax2.set_ylim(0, 100)
ax2.plot(all_checkpoints, self_play_mean_reward_4_0, label="self-play (seed 123)")
ax2.plot(all_checkpoints, self_play_mean_reward_4_1, label="self-play (seed 456)")
ax2.plot(all_checkpoints, cross_play_mean_reward_4, label="cross-play")
ax2.set_xlabel("Episode")

ax3.set_title("8 agents")
ax3.set_ylim(0, 100)
ax3.plot(all_checkpoints, self_play_mean_reward_8_0, label="self-play (seed 123)")
ax3.plot(all_checkpoints, self_play_mean_reward_8_1, label="self-play (seed 456)")
ax3.plot(all_checkpoints, cross_play_mean_reward_8, label="cross-play")
ax3.set_xlabel("Episode")
ax3.legend(bbox_to_anchor=(1, 1), loc="upper left")

In [ ]:
run_name_0 = "hom123"
run_name_1 = "hom456"
config_name = "simple_2"
heterogeneous = False
max_checkpoint = 501
num_episodes = 50
random_start = False

config = load_config(config_name)
config["env_config"]["random_start"] = random_start
self_play_mean_reward_hom_0 = []
self_play_mean_reward_hom_1 = []
cross_play_mean_reward_hom = []
all_checkpoints = list(range(1, max_checkpoint + 1, 25))
for checkpoint in all_checkpoints:
    sp_0, sp_1, cp = cross_play(
        run_name_0, run_name_1, checkpoint, checkpoint, config,
        heterogeneous=heterogeneous, num_episodes=num_episodes
    )
    self_play_mean_reward_hom_0.append(sum(sp_0) / num_episodes)
    self_play_mean_reward_hom_1.append(sum(sp_1) / num_episodes)
    cross_play_mean_reward_hom.append(sum(cp) / num_episodes)

In [ ]:
run_name_0 = "simple_4_random_123"
run_name_1 = "simple_4_random_456"
config_name = "simple_4"
heterogeneous = True
max_checkpoint = 501
num_episodes = 50
random_start = True

config = load_config(config_name)
config["env_config"]["random_start"] = random_start
self_play_mean_reward_random_0 = []
self_play_mean_reward_random_1 = []
cross_play_mean_reward_random = []
all_checkpoints = list(range(1, max_checkpoint + 1, 25))
for checkpoint in all_checkpoints:
    sp_0, sp_1, cp = cross_play(
        run_name_0, run_name_1, checkpoint, checkpoint, config,
        heterogeneous=heterogeneous, num_episodes=num_episodes
    )
    self_play_mean_reward_random_0.append(sum(sp_0) / num_episodes)
    self_play_mean_reward_random_1.append(sum(sp_1) / num_episodes)
    cross_play_mean_reward_random.append(sum(cp) / num_episodes)

In [ ]:
%matplotlib inline
all_checkpoints = list(range(1, 502, 25))
plt.ylim(0, 100)
plt.plot(all_checkpoints, self_play_mean_reward_hom_0, label="self-play (seed 123)")
plt.plot(all_checkpoints, self_play_mean_reward_hom_1, label="self-play (seed 456)")
plt.plot(all_checkpoints, cross_play_mean_reward_hom, label="cross-play")
plt.xlabel("Episode")
plt.ylabel("Reward")
plt.title("2 agents")
# plt.legend(bbox_to_anchor=(1,1), loc="upper left")

In [ ]:
plt.ylim(0, 100)
plt.plot(all_checkpoints, self_play_mean_reward_random_0, label="self-play (seed 123)")
plt.plot(all_checkpoints, self_play_mean_reward_random_1, label="self-play (seed 456)")
plt.plot(all_checkpoints, cross_play_mean_reward_random, label="cross-play")
plt.xlabel("Episode")
plt.ylabel("Reward")
plt.title("4 agents")
# plt.legend(bbox_to_anchor=(1,1), loc="upper left")

In [ ]:
run_names = ["simple_4_123", "simple_4_456", "simple_4_456", "simple_4_123"]
checkpoints = [301, 301, 301, 301]
config = load_config("simple_4")
cross_play, ani = run_evaluation(
    run_names,
    checkpoints,
    config, 
    policy_name="ppo", 
    seed=1,
    heterogeneous=True,
    num_episodes=1,
    record=True
)